In [1]:
import pandas as pd
from urllib import request
import folium
from folium.plugins import TimestampedGeoJson
import json
from geojson import Point, Feature, FeatureCollection, dump

# Get Data

Data was referred from Data is Plural via email subscription

Data is from [NYC Parks and Recreation - Street Tree Planting Locations](https://www.nycgovparks.org/trees/street-tree-planting/locations)



In [2]:
r = request.urlopen('https://www.nycgovparks.org/tree-work-orders/street_tree_planting.csv')

last_build_date = r.readlines()[5].decode('utf-8').split(',')[1].strip('\n')
last_build_date

'"2022-08-03 00:49:47"'

In [3]:
df = pd.read_csv('https://www.nycgovparks.org/tree-work-orders/street_tree_planting.csv', skiprows=7)
df

lng        lat    Borough  ZipCode BuildingNumber  \
0    -73.709503  40.740340     Queens    11004         82-030   
1    -73.954008  40.814634  Manhattan    10027            464   
2    -73.712984  40.735428     Queens    11001         254-04   
3    -73.952187  40.799678  Manhattan    10026             37   
4    -73.876284  40.828165      Bronx    10472           1155   
...         ...        ...        ...      ...            ...   
8180 -73.785172  40.727778     Queens    11366         183-02   
8181 -73.810892  40.777863     Queens    11357         151-41   
8182 -73.708925  40.743219     Queens    11004          81-04   
8183 -73.870720  40.896687      Bronx    10470            143   
8184 -73.903583  40.854817      Bronx    10453            110   

                   StreetName  FiscalYear  PlantingSpaceID  CommunityBoard  \
0                  260 STREET           0           148027             413   
1             WEST 129 STREET           0           156427             109   
2                     84 ROAD           0           177638             413   
3         MALCOLM X BOULEVARD           0           178031             110   
4                MANOR AVENUE           0           191641             209   
...                       ...         ...              ...             ...   
8180           UNION TURNPIKE           0          4309386             408   
8181  WILLETS POINT BOULEVARD           0          4995347             407   
8182               262 STREET           0          4302751             413   
8183          EAST 233 STREET           0          5803374             212   
8184          EAST 181 STREET           0           432549             205   

     PlantingSeason  CityCouncil    TreeID      WOId       WOStatus  \
0        05/31/2022           23    114029  15525248      Completed   
1        05/31/2022            7         0  16644663  Not Completed   
2        05/31/2022           23    142438   8573730      Completed   
3        05/31/2022            9    143233   9138879  Not Completed   
4        05/31/2022           18         0  14343624  Not Completed   
...             ...          ...       ...       ...            ...   
8180     05/31/2022           24  13133256  12931606      Completed   
8181     05/31/2022           19  13133260  14373476      Completed   
8182     05/31/2022           23  13133270  16743002      Completed   
8183     05/31/2022           11  13133286  15866418      Completed   
8184     05/31/2022           14  13134156  13213090      Completed   

            CompletedDate  
0     2021-12-07 00:00:00  
1                     NaN  
2     2021-12-07 00:00:00  
3                     NaN  
4                     NaN  
...                   ...  
8180  2022-05-24 00:00:00  
8181  2022-05-09 00:00:00  
8182  2022-04-21 00:00:00  
8183  2022-06-28 00:00:00  
8184  2022-06-10 00:00:00  

[8185 rows x 15 columns]

In [4]:
df['CompletedDate'] = pd.to_datetime(df['CompletedDate'])
df['PlantingSeason'] = pd.to_datetime(df['PlantingSeason'])

In [5]:
df['CompletedDate'].dt.year.unique()

array([2021.,   nan, 2022., 2016., 2018.])

In [6]:
nyc_map = folium.Map(location=[40.7128, -74.0060], zoom_start=12)
records = df[df['WOStatus'] == 'Completed'][['lat', 'lng', 'CompletedDate']].to_records()

for record in records:
    folium.Marker(location=[record[1], record[2]],
                  icon=folium.Icon(color='green',
                                   icon_color='white',
                                   icon='tree',
                                   prefix='fa',
                                   ),
                  # popup=record[4],
                  tooltip=f"Completed Date: {record[3]}"
                  ).add_to(nyc_map)

nyc_map

In [7]:
def df_to_geojson(df, properties, lat='latitude', lon='longitude'):
    # create a new python dict to contain our geojson data, using geojson format
    geojson = {'type':'FeatureCollection', 'features':[]}

    # loop through each row in the dataframe and convert each row to geojson format
    for _, row in df.iterrows():
        # create a feature template to fill in
        feature = {'type':'Feature',
                   'properties':{},
                   'geometry':{'type':'Point',
                               'coordinates':[]}}

        # fill in the coordinates
        feature['geometry']['coordinates'] = [row[lon],row[lat]]

        # for each column, get the value and add it as a new feature property
        for prop in properties:
            feature['properties'][prop] = row[prop]

        # add this feature (aka, converted dataframe row) to the list of features inside our dict
        geojson['features'].append(feature)

    return geojson

In [8]:
df_for_geojson = df[df['WOStatus'] == 'Completed'].rename({'lat': 'latitude', 'lng': 'longitude', 'CompletedDate': 'times'}, axis=1)
df_for_geojson['times'] = df_for_geojson['times'].astype(str)

geojson = df_to_geojson(df=df_for_geojson, properties=['times'], lat='latitude', lon='longitude')

In [9]:
with open('dataset.geojson', 'w') as f:
    dump(geojson, f)

In [10]:
with open('dataset.geojson') as j:
    data = json.load(j)

In [12]:
nyc_map = folium.Map(location=[40.7128, -74.0060], zoom_start=12)

TimestampedGeoJson(data, transition_time=20).add_to(nyc_map)
nyc_map